In [1]:
import ROOT
from ROOT import TCanvas
from DistROOT import DistTree

Welcome to JupyROOT 6.15/01


In [73]:
def runAnalysis(rdf):

    # Branches clasified by diagonal
    diagonals = {
        # return a tuple: ([left] verticals in 45, [right] verticals in 56))
        "d45b_56t"  : (["track_rp_5", "track_rp_21", "track_rp_25"],
                       ["track_rp_104", "track_rp_120", "track_rp_124"]),
        "ad45b_56b" : (["track_rp_5", "track_rp_21", "track_rp_25"],
                       ["track_rp_105", "track_rp_121", "track_rp_125"]),
        "d45t_56b"  : (["track_rp_4", "track_rp_20", "track_rp_24"],
                       ["track_rp_105", "track_rp_121", "track_rp_125"]),
        "ad45t_56t" : (["track_rp_4", "track_rp_20", "track_rp_24"],
                       ["track_rp_104", "track_rp_120", "track_rp_124"])
    }

    selected_diagonal = "d45b_56t"

    rp_left, rp_right = diagonals[selected_diagonal]
    
    # Columns per branch
    attributes = ['valid', 'x', 'y']

    full_branches = ["{}.{}".format(c,a) for a in attributes for c in rp_left+rp_right ]

    # Split left and right branch on valid, x and y
    valids = [ "(unsigned int) {}".format(v) for v in full_branches[0:6]]
    xs     = full_branches[6:12]
    ys     = full_branches[12:18]

    # Filter and define output branches
    filter_code = """({0}.valid + {1}.valid + {2}.valid ) >= 2 &&
    ({3}.valid + {4}.valid + {5}.valid ) >= 2
    """.format(*(rp_left+rp_right))

    # Input tree
    treename= "TotemNtuple"
    #rdf = RDF(treename, vec_input_files)

    # Filter and define output branches
    r = rdf.Filter(filter_code)  \
           .Define("v_L_1_F", valids[0]) \
           .Define("v_L_2_N", valids[1]) \
           .Define("v_L_2_F", valids[2]) \
           .Define("v_R_1_F", valids[3]) \
           .Define("v_R_2_N", valids[4]) \
           .Define("v_R_2_F", valids[5]) \
           .Define("x_L_1_F", xs[0]) \
           .Define("x_L_2_N", xs[1]) \
           .Define("x_L_2_F", xs[2]) \
           .Define("x_R_1_F", xs[3]) \
           .Define("x_R_2_N", xs[4]) \
           .Define("x_R_2_F", xs[5]) \
           .Define("y_L_1_F", ys[0]) \
           .Define("y_L_2_N", ys[1]) \
           .Define("y_L_2_F", ys[2]) \
           .Define("y_R_1_F", ys[3]) \
           .Define("y_R_2_N", ys[4]) \
           .Define("y_R_2_F", ys[5]) \
           .Define("timestamp",    "(unsigned int) (event_info.timestamp - 1444860000)") \
           .Define("run_num",      "(unsigned int) event_info.run_no")                 \
           .Define("bunch_num",    "trigger_data.bunch_num")            \
           .Define("event_num",    "trigger_data.event_num")            \
           .Define("trigger_num",  "trigger_data.trigger_num")          \
           .Define("trigger_bits", "trigger_data.input_status_bits")

    timestamp_min = 20.9E3
    timestamp_max = 31.5E3
    timestamp_bins = timestamp_max - timestamp_min + 1.;        
    model = ("h_timestamp_dgn", ";timestamp;rate   (Hz)", int(timestamp_bins), timestamp_min-0.5, timestamp_max+0.5)
    h_timestamp_dgn = r.Histo1D(model, "timestamp")

    # Save output tree
    return h_timestamp_dgn

In [77]:

def fillHist(tdf):
    hist = runAnalysis(tdf)
    return hist

In [78]:
def mergeHist(h1, h2):
    h1.Add(h2)
    return h1

In [79]:
dTree = DistTree(filelist = ['root://eostotem//eos/totem/data/cmstotem/2015/90m/Totem/Ntuple/version2/4495/TotemNTuple_9883.040.ntuple.root',],
                 treename = "TotemNtuple",
                 npartitions = 2)

myHist = dTree.ProcessAndMerge(fillHist, mergeHist)

Plot the resulting histogram. Note how we activate the JavaScript graphics of ROOT with the `jsroot` magic.

In [80]:
%jsroot on
c = TCanvas()
myHist.GetXaxis().SetTitle("track_rp_3_x")
myHist.GetYaxis().SetTitle("track_rp_3_y")
myHist.Draw()
c.Draw()